In [1]:
from transformers import AutoTokenizer

#加载分词器
tokenizer = AutoTokenizer.from_pretrained('hfl/rbt6')

print(tokenizer)

#分词测试
tokenizer.batch_encode_plus(
    [[
        '海', '钓', '比', '赛', '地', '点', '在', '厦', '门', '与', '金', '门', '之', '间',
        '的', '海', '域', '。'
    ],
     [
         '这', '座', '依', '山', '傍', '水', '的', '博', '物', '馆', '由', '国', '内', '一',
         '流', '的', '设', '计', '师', '主', '持', '设', '计', '，', '整', '个', '建', '筑',
         '群', '精', '美', '而', '恢', '宏', '。'
     ]],
    truncation=True,
    padding=True,
    return_tensors='pt',
    is_split_into_words=True)

Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


BertTokenizerFast(name_or_path='hfl/rbt6', vocab_size=21128, model_max_length=1000000000000000019884624838656, is_fast=True, padding_side='right', truncation_side='right', special_tokens={'unk_token': '[UNK]', 'sep_token': '[SEP]', 'pad_token': '[PAD]', 'cls_token': '[CLS]', 'mask_token': '[MASK]'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
	0: AddedToken("[PAD]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	100: AddedToken("[UNK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	101: AddedToken("[CLS]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	102: AddedToken("[SEP]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	103: AddedToken("[MASK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
}


{'input_ids': tensor([[ 101, 3862, 7157, 3683, 6612, 1765, 4157, 1762, 1336, 7305,  680, 7032,
         7305,  722, 7313, 4638, 3862, 1818,  511,  102,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0],
        [ 101, 6821, 2429,  898, 2255,  988, 3717, 4638, 1300, 4289, 7667, 4507,
         1744, 1079,  671, 3837, 4638, 6392, 6369, 2360,  712, 2898, 6392, 6369,
         8024, 3146,  702, 2456, 5029, 5408, 5125, 5401, 5445, 2612, 2131,  511,
          102]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [1, 1, 1, 1, 1, 1, 1, 1, 1, 1,

In [2]:
import torch
from datasets import load_dataset, load_from_disk


class Dataset(torch.utils.data.Dataset):
    def __init__(self, split):
        #names=['O', 'B-PER', 'I-PER', 'B-ORG', 'I-ORG', 'B-LOC', 'I-LOC']

        #在线加载数据集
        #dataset = load_dataset(path='peoples_daily_ner', split=split)

        #离线加载数据集
        dataset = load_from_disk(dataset_path='./test_data')[split]

        #过滤掉太长的句子
        def f(data):
            return len(data['tokens']) <= 512 - 2

        dataset = dataset.filter(f)

        self.dataset = dataset

    def __len__(self):
        return len(self.dataset)

    def __getitem__(self, i):
        tokens = self.dataset[i]['tokens']
        labels = self.dataset[i]['ner_tags']

        return tokens, labels


train_dataset = Dataset('train')
validation_dataset = Dataset('validation')

In [3]:
import numpy as np
import torch
from sklearn.metrics import accuracy_score
from data_process import *
from NER.bert_fc.ner_trainer import BertFCTrainer
from NER.vocab import Vocab
from utils import create_batches
from transformers import BertTokenizer
# setup random seed
seed =0
torch.manual_seed(seed)
torch.cuda.manual_seed_all(seed)
np.random.seed(seed)
train_texts,train_labels = [],[]
validation_texts,validation_labels = [],[]
for i in train_dataset:
    text, label = i
    train_texts.append(text)
    train_labels.append(label)

for i in validation_dataset:
    text, label = i
    validation_texts.append(text)
    validation_labels.append(label)


In [4]:
print(train_texts)
# trainer= BertFCTrainer(
#     pretrainerd_model_dir='./model/bert-base-chinese',model_dir='./temp/bertTestNER',learning_rate=5e-5
# )

# trainer.train(
#     train_texts,train_labels,validate_texts = validation_texts, validate_labels = validation_labels, batch_size=64,epoch=8
# )


[['海', '钓', '比', '赛', '地', '点', '在', '厦', '门', '与', '金', '门', '之', '间', '的', '海', '域', '。'], ['这', '座', '依', '山', '傍', '水', '的', '博', '物', '馆', '由', '国', '内', '一', '流', '的', '设', '计', '师', '主', '持', '设', '计', '，', '整', '个', '建', '筑', '群', '精', '美', '而', '恢', '宏', '。'], ['但', '作', '为', '一', '个', '共', '产', '党', '员', '、', '人', '民', '公', '仆', '，', '应', '当', '胸', '怀', '宽', '阔', '，', '真', '正', '做', '到', '“', '先', '天', '下', '之', '忧', '而', '忧', '，', '后', '天', '下', '之', '乐', '而', '乐', '”', '，', '淡', '化', '个', '人', '的', '名', '利', '得', '失', '和', '宠', '辱', '悲', '喜', '，', '把', '改', '革', '大', '业', '摆', '在', '首', '位', '，', '这', '样', '才', '能', '超', '越', '自', '我', '，', '摆', '脱', '世', '俗', '，', '有', '所', '作', '为', '。'], ['在', '发', '达', '国', '家', '，', '急', '救', '保', '险', '十', '分', '普', '及', '，', '已', '成', '为', '社', '会', '保', '障', '体', '系', '的', '重', '要', '组', '成', '部', '分', '。'], ['日', '俄', '两', '国', '国', '内', '政', '局', '都', '充', '满', '变', '数', '，', '尽', '管', '日', '俄', '关', '系', '目', '前', '是', '历', '史', 